In [1]:
import numpy as np
import pandas as pd
import os

import time

os.chdir(r'C:\Users\user\Desktop\add')

In [ ]:
import numpy as np

class uniCUSUM:
    def __init__(self, phase1_len=100, threshold=5, delta=0.5):
        self._delta = float(delta)
        self._threshold = float(threshold)
        self._phase1_len = phase1_len

        # 초기값
        self._mu0 = None
        self._sigma = None
        self._s_prev_pos = 0.0
        self._s_prev_neg = 0.0

        self.violation_upper = []
        self.violation_lower = []   

    # Phase 1
    def fit(self, X: np.ndarray):
        phase1_data = X[:self._phase1_len]

        self._mu0 = np.mean(phase1_data)
        self._sigma = np.std(phase1_data, ddof = 1)
    
    # Phase 2
    def update(self, X: np.ndarray):
        phase2_X = X[self._phase1_len:]

        for idx, x in enumerate(phase2_X):
            s_t_pos = max(0.0, self._s_prev_pos + (x - self._mu0 - self._delta/2) / self._sigma)
            s_t_neg = max(0.0, self._s_prev_neg + (self._mu0 - x - self._delta/2) / self._sigma)

            # 벡터 누적합 업데이트
            self._s_prev_pos = s_t_pos
            self._s_prev_neg = s_t_neg

            if self._s_prev_pos > self._threshold:
                start_idx = self._phase1_len + idx
                self.violation_upper.append(start_idx)

            if self._s_prev_neg > self._threshold:
                start_idx = self._phase1_len + idx
                self.violation_lower.append(start_idx)

        return self.violation_lower, self.violation_upper
    
class multiCUSUM:
    def __init__(self, phase1_len=100, threshold=5, k=1.0):
        self._k = float(k)
        self._threshold = float(threshold)
        self._phase1_len = phase1_len

        # 초기값
        self._mu0 = []
        self._cov0 = []
        self.violation = []

    # Phase 1
    def fit(self, X: np.ndarray):
        X = np.asarray(X, dtype=float)
        phase1_data = X[:self._phase1_len, :]

        self._mu0 = np.mean(phase1_data, axis = 0)
        self._cov0 = np.cov(phase1_data, rowvar = False)

    # Phase 2
    def update(self, X: np.ndarray):
        X = np.asarray(X, dtype=float)

        # 변화가 있는지 T/F만 출력하면 됨
        self.n_t = 1
        self.C_t = np.zeros(X.shape[1]) # 초기 누적합 벡터
        self._inv_cov0 = np.linalg.inv(self._cov0)

        # 시점 t에서의 누적합 벡터
        C_t = np.sum(X - self._mu0, axis = 0)

        # 탐지 통계량
        stat = C_t.T @ self._inv_cov0 @ C_t
        MC_t = max(0, np.sqrt(stat) - self._k * self.n_t)

        result = MC_t > self._threshold

        return result


In [3]:
class CUSUMDetector:
    def __init__(self, phase1_len=50, threshold=5.0, drift=0.5):
        """
        phase1_len: Phase I(기준) 구간 길이 (샘플 수)
        threshold: decision.interval (σ 단위)
        drift: se.shift (σ 단위)
        """
        self.phase1_len = phase1_len
        self.threshold = threshold
        self.drift = drift
        self.reset()

    def reset(self):
        """내부 상태 초기화"""
        self.mean_ = None
        self.sigma_ = None
        self.k = None
        self.h = None
        self.S_pos = 0.0
        self.S_neg = 0.0

    def fit(self, X: np.ndarray):
        """
        Phase I 데이터로부터 μ₀, σ₀, k, h 계산
        X: 1D array-like (phase1_len 길이)
        """
        x1 = np.asarray(X, dtype=float)
        if x1.ndim != 1 or len(x1) < self.phase1_len:
            raise ValueError("fit()에는 길이 phase1_len 이상의 1D 배열을 넣어야 합니다.")
        # 기준 구간
        p1 = x1[:self.phase1_len]
        self.mean_  = p1.mean() # axis = 0 추가해서 평균벡터로 만들기
        self.sigma_ = p1.std(ddof=1) # axis = 0 추가해서 공분산 행렬로 만들기
        # qcc::cusum 매핑
        # k = se.shift * σ₀ / 2
        self.k = (self.drift * self.sigma_) / 2.0
        # h = decision.interval * σ₀
        self.h = self.threshold * self.sigma_
        # 누적합 초기화
        self.S_pos = 0.0
        self.S_neg = 0.0

    def update(self, x: np.ndarray) -> bool:
        """
        Phase II 한 점씩 호출
        x: 단일 관측값 (스칼라)
        Returns:
          True  → S_pos > h 이거나 –S_neg > h 이면 (상향/하향 탐지)
          False → 아직 탐지 아님
        """
        if self.mean_ is None:
            raise RuntimeError("먼저 fit()을 호출하여 Phase I를 설정하세요.")
        xi = float(x)
        s = xi - self.mean_ - self.k
        self.S_pos = max(0.0, self.S_pos + s)
        self.S_neg = min(0.0, self.S_neg + s)
        # 상향 또는 하향 임계 초과 여부
        return (self.S_pos > self.h) or ((-self.S_neg) > self.h)


In [4]:
df = pd.read_csv('Et_H_CO.csv')
df[:20]

time Variable  Value  Label
0      1       X4    331      1
1      1       X5    273      1
2      1       X6    518      1
3      1       X7    572      1
4      1       X8    566      1
5      1       X9    700      1
6      1      X10    629      1
7      1      X11    719      1
8      2       X4    331      1
9      2       X5    274      1
10     2       X6    518      1
11     2       X7    571      1
12     2       X8    566      1
13     2       X9    700      1
14     2      X10    630      1
15     2      X11    719      1
16     3       X4    333      1
17     3       X5    273      1
18     3       X6    518      1
19     3       X7    571      1

In [6]:
def load_data_long(file_path: str):
    df = pd.read_csv(file_path)
    df.columns = df.columns.str.strip()
    pivot = df.pivot_table(
        index=["time", "Label"],
        columns="Variable",
        values="Value",
        aggfunc="first"
    ).sort_index()

    X_raw = pivot.to_numpy(dtype=float)
    y_raw = np.array([lab for (_, lab) in pivot.index], dtype=int)
    return X_raw, y_raw, {c: c for c in np.unique(y_raw)}

X_raw, y_raw, label_mapping = load_data_long("Et_H_CO.csv")

print(X_raw.shape)
print(y_raw.shape)
print(len(label_mapping))

print(X_raw[:8])
print(y_raw[:8])
print(label_mapping)

(11880, 8)
(11880,)
4
[[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [660. 754. 341. 279. 533. 627. 592. 735.]
 [630. 719. 331. 274. 518. 571. 566. 700.]
 [643. 736. 333. 272. 521. 548. 583. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [662. 754. 341. 279. 533. 626. 592. 735.]]
[1 2 3 4 1 2 3 4]
{1: 1, 2: 2, 3: 3, 4: 4}


In [7]:
"""
X_win, y_win 수정, y_win도 동일하게 label...
"""
def create_training_windows(X: np.ndarray, y: np.ndarray, window_size: int, step: int = 1):
    if X.ndim == 2 and X.shape[0] < X.shape[1]:
        X = X.T
    T, F = X.shape
    windows, labels = [], []
    for start in range(0, T - window_size + 1, step):
        end = start + window_size
        X_win = X[start:end]
        y_win = y[start:end]
        windows.append(X_win)
        labels.append(y_win)
        
    X_windows = np.stack(windows)
    y_windows = np.array(labels)
    return X_windows, y_windows

# 2) 슬라이딩 윈도우 생성
window_size = 5
X_train, y_train = create_training_windows(X_raw, y_raw, window_size)

print(X_train.shape)
print(y_train.shape)

print(X_train[:3])
print(y_train[:3])

(11876, 5, 8)
(11876, 5)
[[[629. 719. 331. 273. 518. 572. 566. 700.]
  [644. 737. 334. 272. 521. 548. 584. 727.]
  [665. 759. 342. 275. 531. 598. 593. 739.]
  [660. 754. 341. 279. 533. 627. 592. 735.]
  [630. 719. 331. 274. 518. 571. 566. 700.]]

 [[644. 737. 334. 272. 521. 548. 584. 727.]
  [665. 759. 342. 275. 531. 598. 593. 739.]
  [660. 754. 341. 279. 533. 627. 592. 735.]
  [630. 719. 331. 274. 518. 571. 566. 700.]
  [643. 736. 333. 272. 521. 548. 583. 727.]]

 [[665. 759. 342. 275. 531. 598. 593. 739.]
  [660. 754. 341. 279. 533. 627. 592. 735.]
  [630. 719. 331. 274. 518. 571. 566. 700.]
  [643. 736. 333. 272. 521. 548. 583. 727.]
  [665. 759. 342. 275. 531. 598. 593. 739.]]]
[[1 2 3 4 1]
 [2 3 4 1 2]
 [3 4 1 2 3]]


In [8]:
def create_expanding_windows(X: np.ndarray, y: np.ndarray, min_size: int = 1):
    if X.ndim == 2 and X.shape[0] < X.shape[1]:
        X = X.T
    T, F = X.shape
    windows_list = []
    labels = []
    for end in range(min_size, T + 1):
        win = X[:end]
        windows_list.append(win)
        labels.append(y[end - 1])
    y_windows = np.array(labels)
    return windows_list, y_windows

X_exp, _ = create_expanding_windows(X_raw, y_raw, min_size=1)

print(X_exp[:5])

[array([[629., 719., 331., 273., 518., 572., 566., 700.]]), array([[629., 719., 331., 273., 518., 572., 566., 700.],
       [644., 737., 334., 272., 521., 548., 584., 727.]]), array([[629., 719., 331., 273., 518., 572., 566., 700.],
       [644., 737., 334., 272., 521., 548., 584., 727.],
       [665., 759., 342., 275., 531., 598., 593., 739.]]), array([[629., 719., 331., 273., 518., 572., 566., 700.],
       [644., 737., 334., 272., 521., 548., 584., 727.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [660., 754., 341., 279., 533., 627., 592., 735.]]), array([[629., 719., 331., 273., 518., 572., 566., 700.],
       [644., 737., 334., 272., 521., 548., 584., 727.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [660., 754., 341., 279., 533., 627., 592., 735.],
       [630., 719., 331., 274., 518., 571., 566., 700.]])]


In [21]:
# 20초 동안 흘러들어온다고 가정
cusum = multiCUSUM(phase1_len=100, threshold=5.0)
cusum.fit(X_raw)

In [22]:
mu0 = cusum._mu0
cov0 = cusum._cov0

In [23]:
for i, window in enumerate(X_exp):
    a = cusum.update(window)
    print(a)

False
False
False
False
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
False
False
False
True
True
True
True
True
True
False
False
False
True
False
True
False
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
False
False
True
False
False
False
False
False
False
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


In [ ]:
"""
20초 이후에 가스를 주입한다고 가정하는데,
axis = 0이 되어야 함. 그래야 각 센서에 대한 평균 벡터가 구해지기 때문임.


cusum.fit(X_raw[:20].mean(axis=0))
"""

cusum.fit(X_raw[:20].mean(axis=1))
print(cusum.mean_)
print(cusum.sigma_)
print(cusum.k)
print(cusum.h)

In [25]:
X_raw[:20].mean(axis=0)

array([649.8 , 742.15, 337.15, 274.8 , 525.45, 585.8 , 583.45, 725.35])

552.99375
11.536802881374207
0.0
57.684014406871036


In [ ]:
cusum1 = uniCUSUM(phase1_len=20, threshold=5.0, delta=0.0)
cusum1

In [20]:
cusum1.fit(X_raw[:20].mean(axis=1))
print(cusum1._mu0)
print(cusum1._sigma)

552.99375
11.536802881374207


In [93]:
X_raw[:20]

array([[629., 719., 331., 273., 518., 572., 566., 700.],
       [644., 737., 334., 272., 521., 548., 584., 727.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [660., 754., 341., 279., 533., 627., 592., 735.],
       [630., 719., 331., 274., 518., 571., 566., 700.],
       [643., 736., 333., 272., 521., 548., 583., 727.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [662., 754., 341., 279., 533., 626., 592., 735.],
       [630., 719., 333., 273., 518., 571., 566., 701.],
       [643., 736., 334., 272., 519., 547., 584., 728.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [662., 755., 341., 279., 533., 627., 591., 734.],
       [630., 719., 331., 273., 518., 571., 565., 700.],
       [643., 736., 334., 272., 519., 547., 584., 728.],
       [665., 759., 342., 275., 531., 598., 593., 739.],
       [661., 755., 342., 279., 533., 626., 591., 734.],
       [630., 719., 331., 274., 517., 571., 566., 701.],
       [643., 736., 335., 271.,

In [117]:
"""
확인해보기;
"""
# p1 = x1[:20]
# print(p1.mean()) # axis = 0이 되어야 각 센서에 대한 평균이 나올텐데
# print(p1.std(ddof=1)) # axis = 0이 되어야 각 센서에 대한 표준편차가 나올텐데 ?
phase1_len = 20

p1 = X_raw[:20]
mean = p1.mean(axis = 0)
print(mean)

cov = np.cov(p1, rowvar = False)
print(cov)

# p1 = x1[:phase1_len]
# print(p1)
# # 기준 구간
# p1 = x1[:self.phase1_len]
# self.mean_  = p1.mean() # axis = 0 추가해서 평균벡터로 만들기
# self.sigma_ = p1.std(ddof=1) # axis = 0 추가해서 공분산 행렬로 만들기
# # qcc::cusum 매핑
# # k = se.shift * σ₀ / 2
# self.k = (self.drift * self.sigma_) / 2.0
# # h = decision.interval * σ₀
# self.h = self.threshold * self.sigma_
# # 누적합 초기화
# self.S_pos = 0.0
# self.S_neg = 0.0

[649.8  742.15 337.15 274.8  525.45 585.8  583.45 725.35]
[[211.95789474 236.4         67.29473684  26.01052632  93.67368421
  312.8        154.67368421 211.02105263]
 [236.4        264.66052632  74.55526316  27.66315789 103.19210526
  332.82105263 175.24473684 239.99736842]
 [ 67.29473684  74.55526316  22.13421053   9.24210526  30.87631579
  112.24210526  47.24473684  63.68157895]
 [ 26.01052632  27.66315789   9.24210526   7.64210526  15.30526316
   80.58947368  15.72631579  18.96842105]
 [ 93.67368421 103.19210526  30.87631579  15.30526316  45.31315789
  178.09473684  64.57631579  85.62368421]
 [312.8        332.82105263 112.24210526  80.58947368 178.09473684
  905.11578947 181.46315789 221.38947368]
 [154.67368421 175.24473684  47.24473684  15.72631579  64.57631579
  181.46315789 122.78684211 170.15      ]
 [211.02105263 239.99736842  63.68157895  18.96842105  85.62368421
  221.38947368 170.15       237.60789474]]


In [ ]:
# shift magnitude value 델타


In [71]:
def create_expanding_windows(X: np.ndarray, y: np.ndarray, min_size: int = 1):
    if X.ndim == 2 and X.shape[0] < X.shape[1]:
        X = X.T
    T, F = X.shape
    windows_list = []
    labels = []
    for end in range(min_size, T + 1):
        win = X[:end]
        windows_list.append(win)
        labels.append(y[end - 1])
    y_windows = np.array(labels)
    return windows_list, y_windows

In [137]:
"""
데이터가 1초마다 들어오는 상황
"""

X_exp, _ = create_expanding_windows(X_raw, y_raw, min_size=1)
X_exp

[array([[629., 719., 331., 273., 518., 572., 566., 700.]]),
 array([[629., 719., 331., 273., 518., 572., 566., 700.],
        [644., 737., 334., 272., 521., 548., 584., 727.]]),
 array([[629., 719., 331., 273., 518., 572., 566., 700.],
        [644., 737., 334., 272., 521., 548., 584., 727.],
        [665., 759., 342., 275., 531., 598., 593., 739.]]),
 array([[629., 719., 331., 273., 518., 572., 566., 700.],
        [644., 737., 334., 272., 521., 548., 584., 727.],
        [665., 759., 342., 275., 531., 598., 593., 739.],
        [660., 754., 341., 279., 533., 627., 592., 735.]]),
 array([[629., 719., 331., 273., 518., 572., 566., 700.],
        [644., 737., 334., 272., 521., 548., 584., 727.],
        [665., 759., 342., 275., 531., 598., 593., 739.],
        [660., 754., 341., 279., 533., 627., 592., 735.],
        [630., 719., 331., 274., 518., 571., 566., 700.]]),
 array([[629., 719., 331., 273., 518., 572., 566., 700.],
        [644., 737., 334., 272., 521., 548., 584., 727.],
    

In [168]:
k = 0.5

inv_cov = np.linalg.inv(cov)
results = []

C_t = np.zeros_like(mean)
MC_t_prev = 0
n_t = 1

In [167]:
t = 20

x_t = X_exp[t]
print(x_t.shape)
print(x_t)

diff = x_t - mean
print(diff.shape)
print(diff)


(21, 8)
[[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [660. 754. 341. 279. 533. 627. 592. 735.]
 [630. 719. 331. 274. 518. 571. 566. 700.]
 [643. 736. 333. 272. 521. 548. 583. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [662. 754. 341. 279. 533. 626. 592. 735.]
 [630. 719. 333. 273. 518. 571. 566. 701.]
 [643. 736. 334. 272. 519. 547. 584. 728.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [662. 755. 341. 279. 533. 627. 591. 734.]
 [630. 719. 331. 273. 518. 571. 565. 700.]
 [643. 736. 334. 272. 519. 547. 584. 728.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [661. 755. 342. 279. 533. 626. 591. 734.]
 [630. 719. 331. 274. 517. 571. 566. 701.]
 [643. 736. 335. 271. 521. 549. 583. 726.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [661. 754. 341. 279. 532. 625. 591. 736.]
 [630. 719. 332. 274. 519. 571. 566. 700.]]
(21, 8)
[[-20.8  -23.15  -6.15  -1.8   -7.45 -13.8  -17.45 -25.35]
 [ -5.8   -5.15  -3.1

In [169]:
# cusum 벡터 업데이트
if MC_t_prev > 0:
    C_t += diff
    n_t += 1
else:
    C_t = diff.copy()
    n_t = 1

In [183]:
X_exp[t].mean(axis = 1)

array([538.5  , 545.875, 562.75 , 565.125, 538.625, 545.375, 562.75 ,
       565.25 , 538.875, 545.375, 562.75 , 565.25 , 538.375, 545.375,
       562.75 , 565.125, 538.625, 545.5  , 562.75 , 564.875, 538.875])

In [174]:
(C_t @ inv_cov @ C_t.T).shape

(21, 21)

In [171]:
MC_t = max(0, np.sqrt(C_t @ inv_cov @ C_t.T) - k * n_t)
MC_t_prev = MC_t

c:\Programming\Anaconda\envs\add\lib\site-packages\ipykernel_launcher.py:1: RuntimeWarning: invalid value encountered in sqrt
  """Entry point for launching an IPython kernel.


ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [ ]:
k = 0.5

inv_cov = np.linalg.inv(cov)
results = []

C_t = np.zeros_like(mean)
MC_t_prev = 0
n_t = 1

for t in range(phase1_len+1, len(X_exp)):
    x_t = X_exp[t]
    diff = x_t - mean

    # cusum 벡터 업데이트
    if MC_t_prev > 0:
        C_t += diff
        n_t += 1
    else:
        C_t = diff.copy()
        n_t = 1

    # 탐지 통계량
    MC_t = max(0, np.sqrt(C_t @ inv_cov @ C_t.T) - k * n_t)
    MC_t_prev = MC_t

ValueError: matmul: Input operand 1 has a mismatch in its core dimension 0, with gufunc signature (n?,k),(k,m?)->(n?,m?) (size 8 is different from 168)

In [157]:
C_t.shape # 21.8
inv_cov.shape # 8x8
C_t.T.shape

(8, 21)

In [ ]:
    # 탐지 통계량
    MC_t = max(0, np.sqrt(C_t.T @ inv_cov @ C_t) - k * n_t)
    MC_t_prev = MC_t

array([[-20.8 , -23.15,  -6.15, ..., -13.8 , -17.45, -25.35],
       [ -5.8 ,  -5.15,  -3.15, ..., -37.8 ,   0.55,   1.65],
       [ 15.2 ,  16.85,   4.85, ...,  12.2 ,   9.55,  13.65],
       ...,
       [ 71.2 ,  72.85,  21.85, ..., 119.2 ,  91.55, 127.65],
       [ 80.2 ,  86.85,  21.85, ...,  70.2 , 102.55, 139.65],
       [ 92.2 , 100.85,  25.85, ..., 121.2 , 110.55, 146.65]])

In [142]:
k = 0.5

inv_cov = np.linalg.inv(cov)
results = []

C_t = np.zeros_like(mean)
MC_t_prev = 0
n_t = 1

for t in range(phase1_len, len(X_exp)):
    x_t = X_exp[t]
    diff = x_t - mean

    # cusum 벡터 업데이트
    if MC_t_prev > 0:
        C_t += diff
        n_t += 1
    else:
        C_t = diff.copy()
        n_t = 1

    # 탐지 통계량
    MC_t = max(0, np.sqrt(C_t.T @ inv_cov @ C_t) - k * n_t)
    MC_t_prev = MC_t

    # 이상 탐지 여부
    is_outlier = MC_t > 10
    results.append({
        'index' : t,
        'MC_t' : MC_t,
        'n_t' : n_t,
        'C_t' : C_t.copy()
    })
results

ValueError: matmul: Input operand 1 has a mismatch in its core dimension 0, with gufunc signature (n?,k),(k,m?)->(n?,m?) (size 8 is different from 21)

In [ ]:
"""
패스스
"""
for i, window in enumerate(X_exp):
    if window.shape[0] % window_size != 0:
        continue

0 [[629. 719. 331. 273. 518. 572. 566. 700.]]
1 [[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]]
2 [[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]]
3 [[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [660. 754. 341. 279. 533. 627. 592. 735.]]
5 [[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [660. 754. 341. 279. 533. 627. 592. 735.]
 [630. 719. 331. 274. 518. 571. 566. 700.]
 [643. 736. 333. 272. 521. 548. 583. 727.]]
6 [[629. 719. 331. 273. 518. 572. 566. 700.]
 [644. 737. 334. 272. 521. 548. 584. 727.]
 [665. 759. 342. 275. 531. 598. 593. 739.]
 [660. 754. 341. 279. 533. 627. 592. 735.]
 [630. 719. 331. 274. 518. 571. 566. 700.]
 [643. 736. 333. 272. 521. 548. 583. 727.]
 [665. 759. 342. 275. 531. 598. 593. 